# Easy - Hot Potatoes

In [1]:
from __future__ import annotations

import math
from IPython.display import display
from typing import Generator, List, Union, Any
from rich.pretty import pprint
from dataclasses import dataclass, field
from typing import Any, List

import sys
from pathlib import Path

def find_root_dir(current_path: Path | None = None, marker: str = '.git') -> Path | None:
    """
    Find the root directory by searching for a directory or file that serves as a
    marker.

    Parameters
    ----------
    current_path : Path | None
        The starting path to search from. If None, the current working directory
        `Path.cwd()` is used.
    marker : str
        The name of the file or directory that signifies the root.

    Returns
    -------
    Path | None
        The path to the root directory. Returns None if the marker is not found.
    """
    if not current_path:
        current_path = Path.cwd()
    current_path = current_path.resolve()
    for parent in [current_path, *current_path.parents]:
        if (parent / marker).exists():
            return parent
    return None

root_dir = find_root_dir(marker='omnivault')

if root_dir is not None:
    sys.path.append(str(root_dir))
    from omnivault.dsa.queue.concrete import QueueList
else:
    raise ImportError("Root directory not found.")

## Problem

[Question details can be found here](https://runestone.academy/ns/books/published/pythonds3/BasicDS/SimulationHotPotato.html).

## Constraints and Assumptions

Placeholder.

## Implementation

- `num = 5` means when the counter reaches 5, the person holding the potato will be eliminated.
- d, c, b, a (a is the first in queue and he holds the potato, counter starts at 0)
- a, d, c, b (b holds the potato, counter is 1)
- b, a, d, c (c holds the potato, counter is 2)
- c, b, a, d (d holds the potato, counter is 3)
- d, c, b, a (a holds the potato, counter is 4)
- a, d, c, b (b holds the potato, counter is 5, b is eliminated)

```{figure} ../assets/hot_potato.jpg
---
name: hot_potato
---
Hot Potato elimination diagram, with 4 people and num set to 5.
```

In [3]:
@dataclass(frozen=False, init=True)
class Solution:
    counter: int = 0
    q: QueueList[str] = field(default_factory=QueueList)

    def hot_potato(self, names: List[str], num: int) -> str:
        for name in names:
            self.q.enqueue(name)

        while self.q.size > 1:
            first_in_q = self.q.dequeue()
            self.q.enqueue(first_in_q)

            self.counter += 1
            if self.counter == num:
                self.q.dequeue()
                self.counter = 0  # reset

        return self.q.dequeue()

Note `["Bill", "David", "Susan", "Jane"]` means Bill is first in queue.

In [4]:
print(Solution().hot_potato(names=["Bill", "David", "Susan", "Jane"], num=5)) # Susan

Susan


## Time Complexity

Assume the input `names` to be a list of length $n$.

From {ref}`queue_list_time_complexity`, `dequeue` is of $\O(1)$ since it uses `pop` while `enqueue` is $\O(n)$
since it uses `insert`.

And since we traverse the given list once to `enqueue` first, we would already have $n$ times of `enqueue` which is $\O(n) \times n \approx \O(n^2)$[^ntimesO(n)].

Subsequently, we enter a while loop, which at worst can take $n$ iterations, which eventually leads to $\O(n^2) + \O(n^2) + \O(n) \approx \O(n^2)$.

[^ntimesO(n)]: Note it is not trivial that $n \times \O(n) \approx \O(n^2)$, but for now we treat this result as proven. You can think of it [this way](https://stackoverflow.com/questions/3449441/big-oh-how-can-on-on-on-be-equal-to-on2), if you do something which will take $N$ seconds, and repeat that $N$ times. How many seconds will it take to finish?

## Space Complexity

Assume the queue `q` has length $n$.

The space complexity is at most $\O(n)$ as we are just maintaining a queue with at most $n$ elements inside.